In [7]:
from geovoronoi import voronoi_regions_from_coords
import numpy as np

import json

import networkx as nx

from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, ColorBar, LinearColorMapper, LogColorMapper
import bokeh.palettes

import bokeh.models as bkm
import bokeh.plotting as bkp

from bokeh.io import output_notebook
output_notebook()

from shapely import geometry

from scipy.spatial import Voronoi, Delaunay

Loading BokehJS ...

In [36]:
mapSize = 128

mapBorder = np.array([
    [-mapSize/2, -mapSize/2],
    [-mapSize/2, +mapSize/2],
    [+mapSize/2, +mapSize/2],
    [+mapSize/2, -mapSize/2]
])

mapBorder = geometry.Polygon(mapBorder)

nPolygons = 4096
points = np.random.uniform(low = -mapSize / 2, high = mapSize / 2, size = (nPolygons,2))

In [37]:
# lloyd relaxing
for i in range(2):
    voronoi_polys, voronoi_pts = voronoi_regions_from_coords(points, mapBorder)
    centroids = np.array([[voronoi_polys[i].centroid.x, voronoi_polys[i].centroid.y] for i in range(len(voronoi_polys))])
    idxs = np.array([voronoi_pts[i][0] for i in range(len(voronoi_pts))])
    points[idxs] += (centroids - points[idxs]) * 0.7 # Relax with a factor of 0.7

In [38]:
np.arange(10)

array([0, 1, 2, 3, 4, 5, 6, 7, 8, 9])

In [41]:
# Build Graph
# vor.vertices
# vor.vertices[vor.ridge_points]

# Defination of a cell (polygon)
class Cell():
    def __init__(self, position, polygon):
        self.position = position
        self.polygon = polygon
        self.centroid = np.array([polygon.centroid.x, polygon.centroid.y])

# Class defination; holding the "cell map"
class CellMap():
    
    def __init__(self, mapSize):
        self.mapSize = mapSize
    
    def is_jsonable(self, x):
        try:
            json.dumps(x)
            return True
        except (TypeError, OverflowError):
            return False
    
    def Visualize(self, color = None, colorMapper = LinearColorMapper, palette = None):
        # Draw polygons
        faces = dict(faceXs = [], faceYs = [], color = [], centroidX = [], centroidY = [], **{a: [] for a in self.faces.nodes[0]})
        for k,v in self.faces.nodes(data = True):
            faces['faceXs'].append(list(v['polygon'].exterior.xy[0]))
            faces['faceYs'].append(list(v['polygon'].exterior.xy[1]))
            faces['centroidX'].append(v['centroid'][0])
            faces['centroidY'].append(v['centroid'][1])
            if callable(color):
                faces['color'].append(color(v))
            elif color in v:
                faces['color'].append(float(v[color]))
            else:
                faces['color'].append("#d3e173")
                
            for a in v:
#                 if self.is_jsonable(v[a]):
                faces[a].append(repr(v[a]))
        
        # Face edges
        faceEdge_xs = []
        faceEdge_ys = []
        for edge in self.faces.edges():
            faceEdge_xs.append([self.faces.nodes[edge[0]]['centroid'][0], self.faces.nodes[edge[1]]['centroid'][0]])
            faceEdge_ys.append([self.faces.nodes[edge[0]]['centroid'][1], self.faces.nodes[edge[1]]['centroid'][1]])
            
        # Ridge edges
        ridgeEdge_xs = []
        ridgeEdge_ys = []
        ridgeEdge_colors = []
        for edge in self.ridges.edges(data = True):
            ridgeEdge_xs.append([self.ridges.nodes[edge[0]]['position'][0], self.ridges.nodes[edge[1]]['position'][0]])
            ridgeEdge_ys.append([self.ridges.nodes[edge[0]]['position'][1], self.ridges.nodes[edge[1]]['position'][1]])
            
            # Mark plate borders
            if 'crossPlate' in edge[2] and edge[2]['crossPlate'] == True:
                ridgeEdge_colors.append("#ffffff")
            else:
                ridgeEdge_colors.append("f79428")
        
        color_bar = None
        if palette is not None:
            cmapper = colorMapper(palette = palette)
            poly_fill_color = {'field': "color", "transform": cmapper}
            
            color_bar = ColorBar(color_mapper=cmapper, label_standoff=12)
        else:
            poly_fill_color = {'field': "color"}
        
        p = figure(
            title = "Cell Map, Color = %s" % (color),
            tools = "pan,reset,save,box_zoom,tap,wheel_zoom",
            background_fill_color="#fafafa", 
            plot_width = 720, 
            plot_height = 640,
        )
        
        faces_renderer = p.patches(xs = "faceXs", ys = "faceYs", fill_color = poly_fill_color, source = faces)
        faces_hover = bkm.HoverTool(
            renderers = [faces_renderer], tooltips = [
                ("%s" % a, "@%s" % a) for a in self.faces.nodes[0]
            ]
        )
        p.add_tools(faces_hover)
        
        p.scatter(x = "centroidX", y = "centroidY", color = "#ff3300", source = faces)
        
        p.multi_line(list(faceEdge_xs), list(faceEdge_ys), color = "#40ba8d", alpha = 0.4)
        p.multi_line(list(ridgeEdge_xs), list(ridgeEdge_ys), color = ridgeEdge_colors, alpha = 1.0)
        
        if color_bar is not None:
            p.add_layout(color_bar, 'right')
        
        show(p)
    
    # https://stackoverflow.com/questions/56224824/how-do-i-find-the-circumcenter-of-the-triangle-using-python-without-external-lib
    def CircumCenter(self, T):
        (ax, ay), (bx, by), (cx, cy) = T
        d = 2 * (ax * (by - cy) + bx * (cy - ay) + cx * (ay - by))
        ux = ((ax * ax + ay * ay) * (by - cy) + (bx * bx + by * by) * (cy - ay) + (cx * cx + cy * cy) * (ay - by)) / d
        uy = ((ax * ax + ay * ay) * (cx - bx) + (bx * bx + by * by) * (ax - cx) + (cx * cx + cy * cy) * (bx - ax)) / d
        return (ux, uy)
    
    def GetAttrib(self, G, attribName):
        return [G.nodes[vi][attribName] for vi in range(len(G.nodes))]
        
    def SetAttrib(self, G, attribName, data):
        nx.set_node_attributes(G, {i: data[i] for i in range(len(data))}, attribName)
    
    def CreateVoronoiCells(self, points):
        
        self.N = len(points)
        
        self.voronoi = Voronoi(points)
        self.delaunay = Delaunay(points)

        # Get ridge vertices
        rv = np.asarray(self.voronoi.vertices)

        # Filter out out-of-range points
        outOfRange = np.abs(rv) > self.mapSize/2
        outOfRange = np.logical_or(outOfRange[:, 0], outOfRange[:, 1])
        
#         ridge_index_map = np.arange(rv.shape[0])[np.logical_not(outOfRange)]
        ridge_index_map = np.cumsum(np.logical_not(outOfRange).astype(int)) - 1
        ridge_index_map[outOfRange] = -1
        valid_rvs = rv[np.logical_not(outOfRange)]
        
        ######## Construct ridge graph
        ### Nodes
        self.ridges = nx.Graph()
        self.ridges.add_nodes_from(np.arange(valid_rvs.shape[0]), elevation = 0, flow = 0)
        self.SetAttrib(self.ridges, "position", valid_rvs)
        
        ### Edges
        rvEdges = np.asarray(self.voronoi.ridge_vertices)
        edge_valid = np.logical_and(rvEdges >= 0, np.logical_not(outOfRange)[rvEdges])
        edge_valid = np.logical_and(edge_valid[:, 0], edge_valid[:, 1])
        rvEdges = ridge_index_map[rvEdges]
        
        _evcumsum = np.cumsum(edge_valid) - 1
        
        self.ridges.add_edges_from(rvEdges[edge_valid])
        
        # Get points between the given ridge
        nx.set_edge_attributes(self.ridges, {(rvEdges[ei,0], rvEdges[ei,1]): list(self.voronoi.ridge_points[ei].astype(int)) for ei in range(rvEdges.shape[0])}, "points")
        
        ######## Construct polygon graph
        ### Nodes
        self.faces = nx.Graph()
        self.faces.add_nodes_from(np.arange(points.shape[0]), biome = "None")
        self.SetAttrib(self.faces, "position", points)
        
        ### Polygons
        mapBorder = np.array([
            [-self.mapSize/2, -self.mapSize/2],
            [-self.mapSize/2, +self.mapSize/2],
            [+self.mapSize/2, +self.mapSize/2],
            [+self.mapSize/2, -self.mapSize/2]
        ])

        mapBorder = geometry.Polygon(mapBorder)
        voronoi_polys, voronoi_pts = voronoi_regions_from_coords(points, mapBorder)
        pidxs = np.array([voronoi_pts[i][0] for i in range(len(voronoi_pts))])
        nx.set_node_attributes(self.faces, {pidxs[i]: voronoi_polys[i] for i in range(pidxs.shape[0])}, "polygon")
        nx.set_node_attributes(self.faces, {pidxs[i]: np.array([voronoi_polys[i].centroid.x, voronoi_polys[i].centroid.y]) for i in range(pidxs.shape[0])}, "centroid")
        
        ### Corners
        corners = {}
        isBorder = {}
        for i in range(points.shape[0]):
            pr = self.voronoi.point_region[i]
            if pr < 0:
                corners[i] = []
            else:
                cs = []
                isBorder[i] = False
                for c in self.voronoi.regions[pr]:
                    if c >= 0 and not outOfRange[c]:
                        cs.append(ridge_index_map[c])
                    else:
                        isBorder[i] = True
                corners[i] = cs

        nx.set_node_attributes(self.faces, corners, "corners")
        nx.set_node_attributes(self.faces, isBorder, "isBorder")
        
        # Remove triangles with circumcenter outside the map ( = corresponding voronoi ridge vertex outside the map )
        ccX, ccY = self.CircumCenter(
            ((points[self.delaunay.simplices[:, 0]][:, 0], points[self.delaunay.simplices[:, 0]][:, 1]),
            (points[self.delaunay.simplices[:, 1]][:, 0], points[self.delaunay.simplices[:, 1]][:, 1]),
            (points[self.delaunay.simplices[:, 2]][:, 0], points[self.delaunay.simplices[:, 2]][:, 1]))
        )
        pedge_valid = np.logical_and(np.abs(ccX) <= mapSize / 2, np.abs(ccY) <= mapSize / 2)
        psimplices = self.delaunay.simplices[pedge_valid]
        
        for si, ei in [(0, 1), (1, 2), (2, 0)]:
            self.faces.add_edges_from(np.stack([psimplices[:, si], psimplices[:, ei]], axis = -1))
            
        ### Shortcuts
        self.faceEdges = np.asarray(self.faces.edges())
    
    def GeneratePlates(self, nPlates):
        plateCenters = set(list(np.random.randint(self.N, size = (nPlates,))))
        cells = nx.voronoi_cells(self.faces, plateCenters)
        cells = dict(zip(cells.keys(), map(list, cells.values())))
        
        plateID = np.zeros((self.N,), dtype = int)
        self.plates = []
        for i, plateCenter in enumerate(cells.keys()):
            # TODO: random velocity
            self.plates.append({
                'center': plateCenter,
                'cells': cells[plateCenter],
                'boundary': []
            })
            plateID[cells[plateCenter]] = i
            
        self.SetAttrib(self.faces, "plateID", plateID)
        
        ### Plate boundaries
        self.plateBoundaries = []
        for s, e, data in self.ridges.edges(data = True):
            if self.faces.nodes[data['points'][0]]['plateID'] != self.faces.nodes[data['points'][1]]['plateID']:
                self.ridges.edges[(s, e)]['crossPlate'] = True
                self.plateBoundaries.append((s, e))
                
                self.plates[self.faces.nodes[data['points'][0]]['plateID']]['boundary'].append((s, e))
                self.plates[self.faces.nodes[data['points'][1]]['plateID']]['boundary'].append((s, e))

m = CellMap(mapSize)
m.CreateVoronoiCells(points)
print("CellMap Created")

m.GeneratePlates(7)
m.Visualize(color = "plateID", palette = bokeh.palettes.Category10_10)

# lines = vor.vertices[rv[np.logical_and(rv[:, 0] >= 0, rv[:, 1] >= 0)]]
# line_xs = lines[:,:,0]
# line_ys = lines[:,:,1]

# line_xs.shape

CellMap Created


In [6]:
# Draw points
p = figure(title = "Points", background_fill_color="#fafafa")
p.scatter(x = points[:, 0], y = points[:, 1], color = "#ff3300")

# Voronoi
# voro_x = [list(voronoi_polys[i].exterior.xy[0]) for i in range(len(voronoi_polys))]
# voro_y = [list(voronoi_polys[i].exterior.xy[1]) for i in range(len(voronoi_polys))]
# p.patches(voro_x, voro_y, fill_color = "#ffffff00")

# Voronoi (scipy)
p.multi_line(list(line_xs), list(line_ys))

p.scatter(
    x = [voronoi_polys[i].centroid.x for i in range(len(voronoi_polys))], 
    y = [voronoi_polys[i].centroid.y for i in range(len(voronoi_polys))], 
    color = "#0033ff")

show(p)

NameError: name 'line_xs' is not defined